In [61]:
from gensim.models import Word2Vec
from gensim.utils import simple_preprocess
from sklearn.cluster import KMeans
import numpy as np
import pandas as pd
import os
import gensim.downloader as api
from sklearn.metrics import silhouette_score

In [ ]:
import os

num_threads = os.cpu_count()
print("Numero di thread disponibili:", num_threads)

In [37]:
schema_mediato = pd.read_csv("../datasets/MediatedSchemaSemicolon.csv",sep=";")

In [38]:
schema_mediato

name                         location        marketCap sharePrice  \
0       Lacework          United States, San Jose            $8.3B        NaN   
1        Tipalti         United States, San Mateo            $8.3B        NaN   
2         Tempus           United States, Chicago            $8.1B        NaN   
3        Anduril            United States, Irvine           $8.48B        NaN   
4           Bolt                 Estonia, Tallinn            $8.4B        NaN   
...          ...                              ...              ...        ...   
81701    PepsiCo      Purchase, NY, United States  $241.05 Billion        NaN   
81702     Costco      Issaquah, WA, United States  $258.15 Billion        NaN   
81703   Broadcom      San Jose, CA, United States  $265.27 Billion        NaN   
81704  Coca-Cola       Atlanta, GA, United States  $273.20 Billion        NaN   
81705      Lilly  Indianapolis, IN, United States  $273.01 Billion        NaN   

                      category foundationYear  
0                Cybersecurity           2015  
1                      Fintech           2010  
2                       Health           2015  
3      Artificial intelligence           2017  
4        Auto & transportation           2013  
...                        ...            ...  
81701                      NaN            NaN  
81702                      NaN            NaN  
81703                      NaN            NaN  
81704                      NaN            NaN  
81705                      NaN            NaN  

[81706 rows x 6 columns]

## Utilizzo schema mediato

In [39]:
records = []

In [40]:
for i in range(0,len(schema_mediato)):
    record = schema_mediato.iloc[i].dropna()
    records.append(record.tolist())
    

In [41]:
records

[['Lacework', 'United States, San Jose', '$8.3B', 'Cybersecurity', '2015'],
 ['Tipalti', 'United States, San Mateo', '$8.3B', 'Fintech', '2010'],
 ['Tempus', 'United States, Chicago', '$8.1B', 'Health', '2015'],
 ['Anduril',
  'United States, Irvine',
  '$8.48B',
  'Artificial intelligence',
  '2017'],
 ['Bolt', 'Estonia, Tallinn', '$8.4B', 'Auto & transportation', '2013'],
 ['ByteDance', 'China, Beijing', '$140B', 'Artificial intelligence', '2012'],
 ['Niantic',
  'United States, San Francisco',
  '$9B',
  'Mobile & telecommunications',
  '2015'],
 ['OYO Rooms', 'India, Gurugram', '$9B', 'Travel', '2012'],
 ['Kavak',
  'Mexico, Lerma de Villada',
  '$8.7B',
  'E-commerce & direct-to-consumer',
  '2014'],
 ['Personio',
  'Germany, Munich',
  '$8.5B',
  'Internet software & services',
  '2015'],
 ['Klaviyo',
  'United States, Boston',
  '$9.2B',
  'Internet software & services',
  '2012'],
 ['Rapyd', 'United Kingdom, London', '$8.75B', 'Fintech', '2016'],
 ['Nuro',
  'United States, Mou

In [69]:
model = Word2Vec(sentences=records, vector_size=256, window=5, min_count=1, workers=4)

In [70]:
def calculate_vector(record):
    # Inizializza un vettore vuoto
    record_vector = np.zeros(model.vector_size)
    # Somma i vettori di embedding di ciascun token nel record
    for token in record:
        record_vector += model.wv[token]
    #Normalizza il vettore risultante
    record_vector /= 100
    return record_vector

In [71]:
records

[['Lacework', 'United States, San Jose', '$8.3B', 'Cybersecurity', '2015'],
 ['Tipalti', 'United States, San Mateo', '$8.3B', 'Fintech', '2010'],
 ['Tempus', 'United States, Chicago', '$8.1B', 'Health', '2015'],
 ['Anduril',
  'United States, Irvine',
  '$8.48B',
  'Artificial intelligence',
  '2017'],
 ['Bolt', 'Estonia, Tallinn', '$8.4B', 'Auto & transportation', '2013'],
 ['ByteDance', 'China, Beijing', '$140B', 'Artificial intelligence', '2012'],
 ['Niantic',
  'United States, San Francisco',
  '$9B',
  'Mobile & telecommunications',
  '2015'],
 ['OYO Rooms', 'India, Gurugram', '$9B', 'Travel', '2012'],
 ['Kavak',
  'Mexico, Lerma de Villada',
  '$8.7B',
  'E-commerce & direct-to-consumer',
  '2014'],
 ['Personio',
  'Germany, Munich',
  '$8.5B',
  'Internet software & services',
  '2015'],
 ['Klaviyo',
  'United States, Boston',
  '$9.2B',
  'Internet software & services',
  '2012'],
 ['Rapyd', 'United Kingdom, London', '$8.75B', 'Fintech', '2016'],
 ['Nuro',
  'United States, Mou

In [72]:
records_w2v = []
for i in range(0, len(records)):
    records_w2v.append(calculate_vector(records[i]))

In [73]:
records_w2v

[array([ 3.62411825e-03, -5.88225449e-03, -3.75296058e-03,  3.15005872e-03,
         9.80182465e-03,  1.17770947e-03,  4.53905645e-03, -1.26480679e-03,
        -4.30434208e-03,  5.82677491e-03,  1.44619365e-04, -4.75259085e-03,
         1.24941466e-04, -3.07170866e-03, -3.84398455e-03,  2.70673744e-04,
         2.09477613e-03, -2.96040218e-03, -9.75911237e-03,  1.33423326e-02,
         5.36261158e-03,  3.64885771e-03, -1.57604279e-03, -1.06686231e-02,
        -5.43049417e-03,  4.55348139e-03,  5.73947303e-03, -2.23910024e-03,
        -9.20473678e-05, -8.02731804e-03,  3.70955491e-04,  6.55097520e-03,
        -2.45348604e-03, -7.86978524e-04, -1.50283992e-03,  1.88536390e-03,
         5.73627959e-03, -3.44921208e-03, -3.39891895e-03, -3.14535144e-03,
        -2.81004312e-03,  6.75223474e-03, -3.81258850e-03,  5.02934553e-03,
         9.84851124e-03, -2.21151135e-03, -2.30422686e-04,  1.83258668e-03,
        -2.66912944e-03, -2.30031586e-03, -1.17571516e-03,  1.24383055e-03,
         4.1

In [74]:
df = pd.DataFrame(records_w2v)
df

0         1         2         3         4         5         6    \
0      0.003624 -0.005882 -0.003753  0.003150  0.009802  0.001178  0.004539   
1      0.006348 -0.008576 -0.004938  0.004497  0.013967  0.002702  0.006072   
2      0.004631 -0.007270 -0.004772  0.003882  0.012090  0.001607  0.005468   
3      0.003889 -0.005275 -0.003181  0.002878  0.008692  0.001515  0.003928   
4      0.003571 -0.005519 -0.003090  0.003033  0.008801  0.001036  0.004079   
...         ...       ...       ...       ...       ...       ...       ...   
81701  0.000411 -0.000490 -0.000077  0.000254  0.000640  0.000182  0.000300   
81702  0.000355 -0.000403 -0.000110  0.000218  0.000558  0.000218  0.000244   
81703  0.000847 -0.001040 -0.000342  0.000584  0.001463  0.000297  0.000600   
81704  0.000921 -0.001110 -0.000283  0.000712  0.001587  0.000342  0.000675   
81705  0.000127 -0.000177 -0.000106  0.000121  0.000324  0.000101  0.000121   

            7         8         9    ...       246       247       248  \
0     -0.001265 -0.004304  0.005827  ...  0.001999  0.003209  0.003511   
1     -0.001332 -0.005203  0.006537  ...  0.004595  0.004507  0.004458   
2     -0.001579 -0.005471  0.007309  ...  0.002161  0.003942  0.004500   
3     -0.000879 -0.003200  0.004167  ...  0.002779  0.002759  0.002871   
4     -0.001111 -0.003624  0.004886  ...  0.002106  0.002901  0.003045   
...         ...       ...       ...  ...       ...       ...       ...   
81701  0.000018 -0.000090  0.000085  ...  0.000566  0.000188  0.000149   
81702  0.000034 -0.000009  0.000132  ...  0.000466  0.000202  0.000021   
81703 -0.000039 -0.000148  0.000159  ...  0.001001  0.000493  0.000266   
81704 -0.000073 -0.000223  0.000215  ...  0.001140  0.000540  0.000225   
81705  0.000039 -0.000084 -0.000032  ...  0.000198  0.000093  0.000061   

            249       250       251       252       253       254       255  
0     -0.006788 -0.005333 -0.001319 -0.006094  0.007034 -0.008539  0.002739  
1     -0.009476 -0.006974 -0.002034 -0.007746  0.009162 -0.011391  0.003804  
2     -0.008537 -0.006820 -0.001668 -0.007859  0.008991 -0.010512  0.003532  
3     -0.005871 -0.004359 -0.001071 -0.004953  0.005835 -0.006970  0.002439  
4     -0.006060 -0.004702 -0.001102 -0.005266  0.006095 -0.007638  0.002354  
...         ...       ...       ...       ...       ...       ...       ...  
81701 -0.000416 -0.000249 -0.000096 -0.000183  0.000261 -0.000404  0.000190  
81702 -0.000312 -0.000195 -0.000071 -0.000077  0.000265 -0.000368  0.000163  
81703 -0.000774 -0.000540 -0.000251 -0.000393  0.000557 -0.001054  0.000336  
81704 -0.000955 -0.000511 -0.000237 -0.000387  0.000577 -0.001109  0.000372  
81705 -0.000160 -0.000077 -0.000065 -0.000110  0.000216 -0.000131  0.000082  

[81706 rows x 256 columns]

In [75]:
kmeans = KMeans(n_clusters=800, random_state=0).fit(df)

/Users/alessandropesare/anaconda3/envs/FinalProjectIDD3_8/lib/python3.8/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)


In [76]:
silhouette_score(df,kmeans.labels_)

0.30262498379224256

In [79]:
#Esegui il blocking basato sui cluster ottenuti
blocks = {}  # Dizionario che mappa il cluster al suo insieme di record
for i, label in enumerate(kmeans.labels_):
    if label not in blocks:
        blocks[label] = []
    blocks[label].append(records[i])

print("Blocchi ottenuti:")
print(len(blocks))

Blocchi ottenuti:
800
